In [1]:
import os
import sys
module_path = os.path.abspath(os.path.join('../../..'))
if module_path not in sys.path:
    sys.path.append(module_path)

In [2]:
print(module_path)

/Users/revilooliver/Documents/quantum_computing/research/pauli_sandwitching/cut4mitigation


In [3]:
# author: Ji Liu email: ji.liu@anl.gov

import itertools, numpy
import circuit_cutter
import mlrecon_methods as ml
import numpy as np
import mthree

import qiskit
from qiskit import *
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, Aer, execute, transpile

from qiskit.transpiler import PassManager

from qiskit.converters import circuit_to_dag
from qiskit.visualization import dag_drawer, plot_histogram
from qiskit.compiler import assemble

from qiskit.tools.monitor import job_monitor, backend_monitor, backend_overview

import qiskit.providers.aer.noise as noise
from qiskit.providers.aer.noise import NoiseModel

from utils.utils import filter_results, dict_to_list, H_distance, total_counts, norm_dict
from utils.vqe_utils import read_from_file, MeasureCircuit, find_commute_groups, evaluation, apply_checking_circuit
from mlrecon_methods import run_circuits, collect_fragment_circuits

In [4]:
qiskit.__qiskit_version__

{'qiskit-terra': '0.22.2', 'qiskit-aer': '0.11.1', 'qiskit-ignis': '0.7.1', 'qiskit-ibmq-provider': '0.19.2', 'qiskit': '0.39.2', 'qiskit-nature': '0.5.1', 'qiskit-finance': None, 'qiskit-optimization': None, 'qiskit-machine-learning': None}

In [5]:
numpy.set_printoptions(linewidth = 200)

qubits = 5

simulation_backend = "qasm_simulator"

seed = 0
print_circuits = True

In [6]:
IBMQ.load_account()
provider = IBMQ.get_provider(hub='ibm-q-ornl', group='ornl', project='chm185')
provider.backends()

[<IBMQSimulator('ibmq_qasm_simulator') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_montreal') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_toronto') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_kolkata') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_mumbai') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_lima') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_belem') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_quito') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_guadalupe') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_statevector') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_mps') from IBMQ(hub='ibm-q-ornl', grou

In [7]:
device = provider.get_backend('ibm_auckland')
device

<IBMQBackend('ibm_auckland') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>

In [8]:
device.configuration().to_dict()['max_shots']

100000

In [9]:
from qiskit import IBMQ, Aer
from qiskit.providers.aer.noise import NoiseModel
noise_model = NoiseModel.from_backend(device, gate_error = False, thermal_relaxation= False)
print(noise_model)

NoiseModel:
  Basis gates: ['cx', 'id', 'reset', 'rz', 'sx', 'x']
  Instructions with noise: ['measure']
  Qubits with noise: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26]
  Specific qubit errors: [('measure', (0,)), ('measure', (1,)), ('measure', (2,)), ('measure', (3,)), ('measure', (4,)), ('measure', (5,)), ('measure', (6,)), ('measure', (7,)), ('measure', (8,)), ('measure', (9,)), ('measure', (10,)), ('measure', (11,)), ('measure', (12,)), ('measure', (13,)), ('measure', (14,)), ('measure', (15,)), ('measure', (16,)), ('measure', (17,)), ('measure', (18,)), ('measure', (19,)), ('measure', (20,)), ('measure', (21,)), ('measure', (22,)), ('measure', (23,)), ('measure', (24,)), ('measure', (25,)), ('measure', (26,))]


In [10]:
noisy_simulator = provider.get_backend('ibmq_qasm_simulator')

In [11]:
front_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_front.qasm")

In [12]:
mid_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_mid.qasm")

In [13]:
end_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_end.qasm")

In [14]:
orign_circuit = front_layer + mid_layer + end_layer

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_30806/743480212.py:1: DeprecationWarning: The QuantumCircuit.__add__() method is being deprecated.Use the compose() method which is more flexible w.r.t circuit register compatibility.
  orign_circuit = front_layer + mid_layer + end_layer


In [15]:
orign_circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐           │         »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘                     »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐                      »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘                      »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐                     »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘                     »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────────────────────────»
      └────────────────┘ └────────────────┘                                   »
q_8: ─────────────────────────────────────────────────────────────────────────»
                                                                              »
«        ┌────────────┐                                                      »
«q_0: ───┤ Rz(1.5641) ├──────────────────────────────────────────────────────»
«     ┌──┴────────────┴─┐┌─────────────┐                                     »
«q_1: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─────────────────────────────────────»
«     └─────────────────┘├─────────────┴┐ ┌─────────────┐                    »
«q_2: ─────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├────────────────────»
«              │         └──────────────┘┌┴─────────────┴─┐ ┌──────────────┐ »
«q_3: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├─»
«                               │        └────────────────┘┌┴──────────────┴┐»
«q_4: ──────────────────────────■────────────────■─────────┤ Ry(-8.148e-06) ├»
«                                                │         └────────────────┘»
«q_5: ───────────────────────────────────────────■─────────────────■─────────»
«                                                                  │         »
«q_6: ─────────────────────────────────────────────────────────────■─────────»
«                                                                            »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_8: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«                                                           
«q_0: ──────────────────────────────────────────────────────
«                                                           
«q_1: ──────────────────────────────────────────────────────
«                                                           
«q_2: ──────────────────────────────────────────────────────
«                                                           
«q_3: ──────────────────────────────────────────────────────
«        ┌────────────┐                                     
«q_4: ───┤ Rz(1.0747) ├─────────────────────────────────────
«     ┌──┴────────────┴─┐  ┌──────────────┐                 
«q_5: ┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─────────────────
«     └─────────────────┘┌─┴──────────────┴┐┌─────────────┐ 
«q_6: ─────────■─────────┤ Ry(-8.1451e-06) ├┤ Rz(0.25427) ├─
«              │         └┬────────────────┤├─────────────┴┐
«q_7: ─────────■──────────┤ Ry(-0.0044055) ├┤ Rz(0.010242) ├
«              

In [16]:
#checking circuit

In [17]:
phase_y_front = [6.827165202923369e-06,-1.6337052388981617e-05, -1.9504648473842978e-05, -4.583505307611714e-05, 6.10354282870864e-05, 5.965270087646158e-06, 9.312744374460134e-06, -0.0043764639879769]
phase_z_front = [1.7168697590535538, 1.5283131502120553, 1.8467840590281954, 1.9183949883797635, 1.8180451683566035, 1.8290020607579571,1.7186918294701956 ,0.0005809279491065732 ]
phase_y_end = [1.7553477050418194e-05, -5.2173015630282704e-06, 2.7300161977647244e-05, 1.6108036965651842e-06,-8.147972934398958e-06, -8.65422271101483e-06, -8.145059343430974e-06, -0.0044055233224810164]
phase_z_end = [1.5640736434660867, 0.8907239659216719, 0.8895530769206249, -0.12591739710453853, 1.0747017329581952, -0.21554369415117478, 0.25426734596118483, 0.010241971123548377]
x_front = [True, False, True, False, True, False, True, False]

In [18]:
qubit_id = 0
circuit = QuantumCircuit(9)
apply_checking_circuit(circuit, [qubit_id], [8], side = 'front', phase_y = phase_y_front[qubit_id], phase_z = phase_z_front[qubit_id], x = x_front[qubit_id])
circuit += orign_circuit
apply_checking_circuit(circuit, [qubit_id], [8], side = 'end', phase_y = phase_y_end[qubit_id], phase_z = phase_z_end[qubit_id])

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_30806/2491252378.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  circuit += orign_circuit


In [19]:
circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘ │                »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼────────────────»
      └─────┬───┬──────┘ └────────────────┘               │                »
q_8: ───────┤ H ├─────────────────────────────────────────■────────────────»
            └───┘                                                          »
«     ┌─────────────────┐┌───┐┌───┐┌────────────────┐┌────────────┐   »
«q_0: ┤ Ry(-6.8272e-06) ├┤ X ├┤ X ├┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─»
«     └─────────────────┘└───┘└───┘└────────────────┘└────────────┘ │ »
«q_1: ──────────────────────────────────────────────────────────────■─»
«                                                                     »
«q_2: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_3: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_4: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_5: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_6: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_7: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_8: ────────────────────────────────────────────────────────────────»
«                                                                     »
«     ┌────────────────┐   ┌────────────┐  ┌─────────────┐ ┌─────────────────┐»
«q_0: ┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├──┤ Rz(-1.5641) ├─┤ Ry(-1.7553e-05) ├»
«     └────────────────┘┌──┴────────────┴─┐├─────────────┤ └─────────────────┘»
«q_1: ────────■─────────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├────────────────────»
«             │         └─────────────────┘├─────────────┴┐  ┌─────────────┐  »
«q_2: ────────■──────────────────■─────────┤ Ry(2.73e-05) ├──┤ Rz(0.88955) ├──»
«                                │         └──────────────┘ ┌┴─────────────┴─┐»
«q_3: ───────────────────────────■────────────────■─────────┤ Ry(1.6108e-06) ├»
«                                                 │         └────────────────┘»
«q_4: ────────────────────────────────────────────■─────────────────■─────────»
«                                                                   │         »
«q_5: ──────────────────────────────────────────────────────────────■─────────»
«                                                                             »
«q_6: ────────────────────────────────────────────────────────────────────────»
«                                                            

In [20]:
pauli_list = read_from_file('HF_hamiltonian.txt')
pauli_commute = find_commute_groups(pauli_list)

In [21]:
#generate individual measurment circuits that changes the basis
meas_qcs = []
for i in range(0, len(pauli_commute)):
    temp_qc = MeasureCircuit(pauli_commute[i], num_qubits = 8,num_qargs = 9)
    meas_qcs.append(temp_qc)
    print(temp_qc)

YXXYYXXY
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_3: ┤ U(π/2,0,π/2) ├
     ├──────────────┤
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
XXXXYXXY
      ┌────────────┐ 
q_0: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_3: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
YXXYXXXX
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     

In [22]:
circuit_list = []
for meas in meas_qcs:
    temp_circuit = circuit.copy()
    temp_circuit += meas
    circuit_list.append(temp_circuit)

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_30806/1717817760.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  temp_circuit += meas


In [23]:
circuit_list[-2].draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘ │                »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼────────────────»
      └─────┬───┬──────┘ └────────────────┘               │                »
q_8: ───────┤ H ├─────────────────────────────────────────■────────────────»
            └───┘                                                          »
«     ┌─────────────────┐┌───┐┌───┐┌────────────────┐┌────────────┐   »
«q_0: ┤ Ry(-6.8272e-06) ├┤ X ├┤ X ├┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─»
«     └─────────────────┘└───┘└───┘└────────────────┘└────────────┘ │ »
«q_1: ──────────────────────────────────────────────────────────────■─»
«                                                                     »
«q_2: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_3: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_4: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_5: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_6: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_7: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_8: ────────────────────────────────────────────────────────────────»
«                                                                     »
«     ┌────────────────┐   ┌────────────┐  ┌─────────────┐ ┌─────────────────┐»
«q_0: ┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├──┤ Rz(-1.5641) ├─┤ Ry(-1.7553e-05) ├»
«     └────────────────┘┌──┴────────────┴─┐├─────────────┤ └─────────────────┘»
«q_1: ────────■─────────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├────────────────────»
«             │         └─────────────────┘├─────────────┴┐  ┌─────────────┐  »
«q_2: ────────■──────────────────■─────────┤ Ry(2.73e-05) ├──┤ Rz(0.88955) ├──»
«                                │         └──────────────┘ ┌┴─────────────┴─┐»
«q_3: ───────────────────────────■────────────────■─────────┤ Ry(1.6108e-06) ├»
«                                                 │         └────────────────┘»
«q_4: ────────────────────────────────────────────■─────────────────■─────────»
«                                                                   │         »
«q_5: ──────────────────────────────────────────────────────────────■─────────»
«                                                                             »
«q_6: ────────────────────────────────────────────────────────────────────────»
«                                                            

In [24]:
# cuts = []
# for i in range(0, 1):
#     if i == 0 or i == qubits - 1:
#         cut = [(circuit.qubits[i], 5),(circuit.qubits[i], 6)]
#     else:
#         cut = [(circuit.qubits[i], 5),(circuit.qubits[i], 4)]
#     cuts += cut

In [25]:
cuts = [(circuit.qubits[0], 7),(circuit.qubits[0], 13)]

In [26]:
fragments_list = []
wire_path_map_list = []
for temp_qc in circuit_list:
    print(temp_qc)
    fragments, wire_path_map = circuit_cutter.cut_circuit(temp_qc, cuts)
    fragments_list.append(fragments)
    wire_path_map_list.append(wire_path_map)

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

...

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

            ┌───┐        ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └─────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────┼────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐ │                »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─┼────────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │                »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                »

In [27]:
print(wire_path_map_list[0])

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(3, 'q'), 0)), (1, Qubit(QuantumRegister(8, 'q'), 7)), (0, Qubit(QuantumRegister(3, 'q'), 2))), Qubit(QuantumRegister(9, 'q'), 1): ((1, Qubit(QuantumRegister(8, 'q'), 3)),), Qubit(QuantumRegister(9, 'q'), 2): ((1, Qubit(QuantumRegister(8, 'q'), 1)),), Qubit(QuantumRegister(9, 'q'), 3): ((1, Qubit(QuantumRegister(8, 'q'), 5)),), Qubit(QuantumRegister(9, 'q'), 4): ((1, Qubit(QuantumRegister(8, 'q'), 2)),), Qubit(QuantumRegister(9, 'q'), 5): ((1, Qubit(QuantumRegister(8, 'q'), 0)),), Qubit(QuantumRegister(9, 'q'), 6): ((1, Qubit(QuantumRegister(8, 'q'), 6)),), Qubit(QuantumRegister(9, 'q'), 7): ((1, Qubit(QuantumRegister(8, 'q'), 4)),), Qubit(QuantumRegister(9, 'q'), 8): ((0, Qubit(QuantumRegister(3, 'q'), 1)),)}


In [28]:
total_variants = ml.fragment_variants(wire_path_map_list[0])

In [29]:
total_variants

24

In [30]:
shots = 10000 * total_variants

In [31]:
fragments_list[0][0].draw()

┌───┐      ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ─────┤ X ├──────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
          ├───┤      └────────────────┘└────────────┘ │ └─────────────┘»
q_1: ─────┤ H ├───────────────────────────────────────■────────■───────»
     ┌────┴───┴────┐┌─────────────────┐                        │       »
q_2: ┤ Rz(-1.5641) ├┤ Ry(-1.7553e-05) ├────────────────────────■───────»
     └─────────────┘└─────────────────┘                                »
«     ┌─────────────────┐    ┌───┐                     
«q_0: ┤ Ry(-6.8272e-06) ├────┤ X ├─────────────────────
«     └──────┬───┬──────┘    └───┘                     
«q_1: ───────┤ H ├─────────────────────────────────────
«      ┌─────┴───┴──────┐┌────────────┐┌──────────────┐
«q_2: ─┤ Ry(1.7553e-05) ├┤ Rz(1.5641) ├┤ U(π/2,0,π/2) ├
«      └────────────────┘└────────────┘└──────────────┘

In [32]:
fragment_cuts_list = []
for index in range(0, len(fragments_list)):
    for idx, fragment in enumerate(fragments_list[index]):
        print(f"fragment {idx}:")
        print(fragment)
        print()
    fragment_cuts = ml.fragment_cuts(wire_path_map_list[index])
    fragment_cuts_list.append(fragment_cuts)


fragment 0:
          ┌───┐      ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ─────┤ X ├──────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
          ├───┤      └────────────────┘└────────────┘ │ └─────────────┘»
q_1: ─────┤ H ├───────────────────────────────────────■────────■───────»
     ┌────┴───┴────┐┌─────────────────┐                        │       »
q_2: ┤ Rz(-1.5641) ├┤ Ry(-1.7553e-05) ├────────────────────────■───────»
     └─────────────┘└─────────────────┘                                »
«     ┌─────────────────┐    ┌───┐                     
«q_0: ┤ Ry(-6.8272e-06) ├────┤ X ├─────────────────────
«     └──────┬───┬──────┘    └───┘                     
«q_1: ───────┤ H ├─────────────────────────────────────
«      ┌─────┴───┴──────┐┌────────────┐┌──────────────┐
«q_2: ─┤ Ry(1.7553e-05) ├┤ Rz(1.5641) ├┤ U(π/2,0,π/2) ├
«      └────────────────┘└────────────┘└──────────────┘

fragment 1:
      ┌────────────────┐   ┌───────────┐                                

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

...

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

fragment 0:
          ┌───┐      ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ─────┤ X ├──────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
          ├───┤      └────────────────┘└────────────┘ │ └─────────────┘»
q_1: ─────┤ H ├───────────────────────────────────────■────────■───────»
     ┌────┴───┴────┐┌─────────────────┐                        │       »
q_2: ┤ Rz(-1.5641) ├┤ Ry(-1.7553e-05) ├────────────────────────■───────»
     └─────────────┘└─────────────────┘                                »
«     ┌─────────────────┐    ┌───┐     
«q_0: ┤ Ry(-6.8272e-06) ├────┤ X ├─────
«     └──────┬───┬──────┘    └───┘     
«q_1: ───────┤ H ├─────────────────────
«      ┌─────┴───┴──────┐┌────────────┐
«q_2: ─┤ Ry(1.7553e-05) ├┤ Rz(1.5641) ├
«      └────────────────┘└────────────┘

fragment 1:
      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘

      ┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────

In [33]:
print(fragment_cuts_list[-1])

[{'prep': 1, 'meas': 1}, {'prep': 1, 'meas': 1}]


In [34]:
wire_path_map

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(3, 'q'), 0)),
  (1, Qubit(QuantumRegister(8, 'q'), 7)),
  (0, Qubit(QuantumRegister(3, 'q'), 2))),
 Qubit(QuantumRegister(9, 'q'), 1): ((1, Qubit(QuantumRegister(8, 'q'), 3)),),
 Qubit(QuantumRegister(9, 'q'), 2): ((1, Qubit(QuantumRegister(8, 'q'), 1)),),
 Qubit(QuantumRegister(9, 'q'), 3): ((1, Qubit(QuantumRegister(8, 'q'), 5)),),
 Qubit(QuantumRegister(9, 'q'), 4): ((1, Qubit(QuantumRegister(8, 'q'), 2)),),
 Qubit(QuantumRegister(9, 'q'), 5): ((1, Qubit(QuantumRegister(8, 'q'), 0)),),
 Qubit(QuantumRegister(9, 'q'), 6): ((1, Qubit(QuantumRegister(8, 'q'), 6)),),
 Qubit(QuantumRegister(9, 'q'), 7): ((1, Qubit(QuantumRegister(8, 'q'), 4)),),
 Qubit(QuantumRegister(9, 'q'), 8): ((0, Qubit(QuantumRegister(3, 'q'), 1)),)}

In [35]:
num_fragments = len(fragments)
num_fragments

2

In [36]:
num_tomo_circuits = len(meas_qcs)
num_tomo_circuits

76

In [37]:
fragments[0].draw()

┌───┐      ┌────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ─────┤ X ├──────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Rz(-1.7169) ├»
          ├───┤      └────────────────┘└────────────┘ │ └─────────────┘»
q_1: ─────┤ H ├───────────────────────────────────────■────────■───────»
     ┌────┴───┴────┐┌─────────────────┐                        │       »
q_2: ┤ Rz(-1.5641) ├┤ Ry(-1.7553e-05) ├────────────────────────■───────»
     └─────────────┘└─────────────────┘                                »
«     ┌─────────────────┐    ┌───┐                   
«q_0: ┤ Ry(-6.8272e-06) ├────┤ X ├───────────────────
«     └──────┬───┬──────┘    └───┘                   
«q_1: ───────┤ H ├───────────────────────────────────
«      ┌─────┴───┴──────┐┌────────────┐┌────────────┐
«q_2: ─┤ Ry(1.7553e-05) ├┤ Rz(1.5641) ├┤ U(π/2,0,π) ├
«      └────────────────┘└────────────┘└────────────┘

In [38]:
fragments[1].draw()

┌────────────────┐   ┌───────────┐                                      »
q_0: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_1: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
            ├───┤       └┬────────────────┤├───────────┬┘           │         »
q_2: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├────────────┼─────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘            │         »
q_3: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_4: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
     ┌┴────────────────┤ └─┬────────────┬─┘               │                   »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐ │                   »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
            ├───┤        ├────────────────┤├────────────┤ │ ┌────────────────┐»
q_7: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            └───┘        └────────────────┘└────────────┘   └────────────────┘»
«                                                                             »
«q_0: ───────────────────────────────────────────────────────────■──────────■─»
«                     ┌──────────────┐ ┌─────────────┐           │          │ »
«q_1: ──────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├───────────┼──────────┼─»
«           │         └──────────────┘ └─────────────┘           │          │ »
«q_2: ──────┼──────────────────────────────────────────■─────────■──────────┼─»
«           │       ┌─────────────────┐┌─────────────┐ │                    │ »
«q_3: ──────┼───────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─┼────────────────────┼─»
«           │       └─────────────────┘└─────────────┘ │                    │ »
«q_4: ──────┼──────────────────────────────────────────┼────────────────────┼─»
«           │                                          │ ┌────────────────┐ │ »
«q_5: ──────■──────────────────────────────────────────■─┤ Ry(1.6108e-06) ├─┼─»
«                                                        └────────────────┘ │ »
«q_6: ──────────────────────────────────────────────────────────────────────■─»
«     ┌────────────┐                                                          »
«q_7: ┤ Rz(1.5641) ├──────────────────────────────────────────────────────────»
«     └────────────┘                                                          »
«     ┌─────────────────┐┌──────────────┐                                   
«q_0: ┤ Ry(-8.6542e-06) ├┤ Rz(-0.21554) ├───────────────────────────────────
«     └─────────────────┘└──────────────┘                                   
«q_1: ──────────────────────────────────────────────────────────────────────
«      ┌────────────────┐ ┌────────────┐                                    
«q_2: ─┤ Ry(-8.148e-06) ├─┤ Rz(1.0747) ├────────────────────────────────────
«      └────────────────┘ └────────────┘                                    
«q_3: ──────────────────────────────────────────────────────────────────────
«                                         ┌────────────────┐┌──────────────┐
«q_4: ──────────────────────────■─────────┤ Ry(-0.0044055) ├┤ Rz(0.010242) ├
«       ┌──────────────┐        │         └────────────────┘└──────────────┘
«q_5: ──┤ Rz(-0.12592) ├────────┼───────────────────────────────────────────
«       └──────────────┘        │        ┌─────────────────┐┌─────────────┐ 
«q_6: ──────────────────────────■────────┤ Ry(-8.1451e-06) ├┤ Rz(0.25427) ├─
«                                        └─────────────────┘└─────────────┘ 
«q_7: ──────────────────────────────────────────────────────────────────────
«

In [39]:
hardware_index = 1

In [40]:
print(shots)

240000


In [41]:
tomography_circuits = []
for idx in range(0, len(fragments_list)):
    fragments = fragments_list[idx]
    wire_path_map = wire_path_map_list[idx]
    temp_frag_circuits = [0] * len(fragments)
    for i in range(0, len(fragments)):
        if i == hardware_index:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
        else:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
    tomography_circuits.append(temp_frag_circuits)

In [42]:
#contains 34 basis
len(tomography_circuits)

76

In [43]:
#contains two fragments
len(tomography_circuits[0])

2

In [44]:
len(tomography_circuits[0][1])

1

In [45]:
#tomography circuits
len(tomography_circuits[0][1][0])

12

In [46]:
multi_exp_circuits = [[],[]]
for i in range(0, len(tomography_circuits)):
    #for each basis collect the three fragments:
    for j in range(0, num_fragments):
        fragment_circ = tomography_circuits[i][j][0]
        multi_exp_circuits[j] += fragment_circ

In [47]:
#[9,8,11,14,13,12,10,7]
#73152064
#[12,11,13,8,7,14,10,9]

In [49]:
multi_exp_circuits[hardware_index][-200].draw()

░  ┌────────────────┐   ┌───────────┐   »
   q_0: ────────────────────░──┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├───»
                            ░  └─────┬───┬──────┘┌──┴───────────┴──┐»
   q_1: ────────────────────░────────┤ X ├───────┤ Ry(-1.9505e-05) ├»
                            ░        ├───┤       └┬────────────────┤»
   q_2: ────────────────────░────────┤ X ├────────┤ Ry(6.1035e-05) ├»
                            ░ ┌──────┴───┴──────┐ └─┬────────────┬─┘»
   q_3: ────────────────────░─┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──»
                            ░ └┬────────────────┤ ┌─┴────────────┴─┐»
   q_4: ────────────────────░──┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├»
                            ░ ┌┴────────────────┤ └─┬────────────┬─┘»
   q_5: ────────────────────░─┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──»
                            ░ └──────┬───┬──────┘ ┌─┴────────────┴─┐»
   q_6: ────────────────────░────────┤ X ├────────┤ Ry(9.3127e-06) ├»
        ┌─────────────────┐ ░        ├───┤        ├────────────────┤»
   q_7: ┤ U3(-1.9106,π,0) ├─░────────┤ X ├────────┤ Ry(6.8272e-06) ├»
        └─────────────────┘ ░        └───┘        └────────────────┘»
c119_0: ════════════════════════════════════════════════════════════»
                                                                    »
c119_1: ════════════════════════════════════════════════════════════»
                                                                    »
c119_2: ════════════════════════════════════════════════════════════»
                                                                    »
c119_3: ════════════════════════════════════════════════════════════»
                                                                    »
c119_4: ════════════════════════════════════════════════════════════»
                                                                    »
c119_5: ════════════════════════════════════════════════════════════»
                                                                    »
c119_6: ════════════════════════════════════════════════════════════»
                                                                    »
c119_7: ════════════════════════════════════════════════════════════»
                                                                    »
«                                                                            »
«   q_0: ────────────────────────────────────────────────────────────────────»
«        ┌────────────┐                                     ┌──────────────┐ »
«   q_1: ┤ Rz(1.8468) ├───────────■───────────────■─────────┤ Ry(2.73e-05) ├─»
«        ├───────────┬┘           │               │         └──────────────┘ »
«   q_2: ┤ Rz(1.818) ├────────────┼───────────────┼──────────────────────────»
«        └───────────┘            │               │       ┌─────────────────┐»
«   q_3: ───────────────■─────────■───────────────┼───────┤ Ry(-5.2173e-06) ├»
«                       │                         │       └─────────────────┘»
«   q_4: ───────────────┼─────────────────────────┼──────────────────────────»
«                       │                         │                          »
«   q_5: ───────────────┼─────────────────────────■──────────────────────────»
«        ┌────────────┐ │                                                    »
«   q_6: ┤ Rz(1.7187) ├─┼────────────────────────────────────────────────────»
«        ├────────────┤ │ ┌────────────────┐┌────────────┐                   »
«   q_7: ┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├┤ Rz(1.5641) ├───────────────────»
«        └────────────┘   └────────────────┘└────────────┘                   »
«c119_0: ════════════════════════════════════════════════════════════════════»
«                                                                            »
«c119_1: ════════════════════════════════════════════════════════════════════»
«                                                                            »
«c119_2: ══════════════════════════════════════════════════

In [63]:
len(multi_exp_circuits[0])

408

In [50]:
frag_datas = [0] * num_fragments
for i in range(0, num_fragments):
    if i == hardware_index:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = [12,11,13,8,7,14,10,9],
                                     backend = device, shots = shots // total_variants, 
                                     optimization_level = 3, monitor_jobs = True)
    else:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = None,
                                     backend = simulation_backend, shots = shots // total_variants,
                                     optimization_level = 3, monitor_jobs = True, noise_model = None)
       

job_id:  99109b99-aa08-4294-b63d-c5b085204966
Job Status: job has successfully run
jobset_id:  977a43d9aed84f5bb4befa06c991d173-16705149883922539


In [51]:
frag_datas[1]

In [51]:
# from qiskit.providers.ibmq.managed import IBMQJobManager
# job_manager = IBMQJobManager()

In [67]:
# job_set = job_manager.retrieve_job_set(job_set_id='973c2fdceaf547389a770d19aad463d8-1669966038684177', provider=provider)

In [68]:
# managed_results = job_set.results()

In [52]:
frag_datas1_copy = frag_datas[1].copy()

In [53]:
frag_datas[1] = [frag_datas[1][0].combine_results()]

In [54]:
# frag_datas[0] = run_circuits(multi_exp_circuits[0], initial_layout = None,
#                              backend = simulation_backend, shots = shots // total_variants,
#                              optimization_level = 3, monitor_jobs = True, noise_model = None)

In [55]:
frag_datas[0][0].results[0].header.name

"(('S0', 'S0', 'S0'), ('Z', 'Z', 'Z'))"

In [56]:
num_tomo_circuits

76

In [57]:
test = [[], []]

In [58]:
results_list = [[], []]
counts_list = [[], []] 
for i in range(0, num_fragments): 
    for j in range(0, num_tomo_circuits):
        start_idx = j * 12
        end_idx = (j + 1) * 12
        results_list[i].append(frag_datas[i][0].results[start_idx : end_idx])
        counts_list[i].append(frag_datas[i][0].get_counts()[start_idx : end_idx])


In [59]:
from mlrecon_methods import organize_tomography_data_from_list
organized_data = []
for i in range(0, num_tomo_circuits):
    frag_data = []
    frag_targets = ml.identify_frag_targets(wire_path_map_list[i])
    for j in range(0, num_fragments):
        frag_data.append(organize_tomography_data_from_list(results_list[j][i], counts_list[j][i],
                                              frag_targets[j].get("prep"),
                                              frag_targets[j].get("meas"),
                                              prep_basis = "SIC", extra_qc = []))
    organized_data.append(frag_data)

(('S0', 'S0', 'S0'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S0') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S0'), ('Z', 'Z', 'Z')) ('S0',) ('Z',) [2] [0]
(('S0', 'S0', 'S0'), ('X', 'Z', 'Z')) ('S0', 'S0', 'S0') ('X', 'Z', 'Z')
(('S0', 'S0', 'S0'), ('X', 'Z', 'Z')) ('S0',) ('X',) [2] [0]
(('S0', 'S0', 'S0'), ('Y', 'Z', 'Z')) ('S0', 'S0', 'S0') ('Y', 'Z', 'Z')
(('S0', 'S0', 'S0'), ('Y', 'Z', 'Z')) ('S0',) ('Y',) [2] [0]
(('S0', 'S0', 'S1'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S1') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S1'), ('Z', 'Z', 'Z')) ('S1',) ('Z',) [2] [0]
(('S0', 'S0', 'S1'), ('X', 'Z', 'Z')) ('S0', 'S0', 'S1') ('X', 'Z', 'Z')
(('S0', 'S0', 'S1'), ('X', 'Z', 'Z')) ('S1',) ('X',) [2] [0]
(('S0', 'S0', 'S1'), ('Y', 'Z', 'Z')) ('S0', 'S0', 'S1') ('Y', 'Z', 'Z')
(('S0', 'S0', 'S1'), ('Y', 'Z', 'Z')) ('S1',) ('Y',) [2] [0]
(('S0', 'S0', 'S2'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S2') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S2'), ('Z', 'Z', 'Z')) ('S2',) ('Z',) [2] [0]
(('S0', 'S0', 'S2'), ('X', 'Z', 'Z')) ('S0', 'S0', 'S2') ('X',

(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Y')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Y')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Y')) ('S0',) ('Y',) [7] [7]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S1'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S1') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S1'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S1',) ('Z',) [7] [7]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S1'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'X')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S1') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'X')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S1'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'X')) ('S1',) ('X',) [7] [7]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S1'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Y')) ('S0', 'S0

(('S0', 'S0', 'S1'), ('X', 'Z', 'Z')) ('S1',) ('X',) [2] [0]
(('S0', 'S0', 'S1'), ('Y', 'Z', 'Z')) ('S0', 'S0', 'S1') ('Y', 'Z', 'Z')
(('S0', 'S0', 'S1'), ('Y', 'Z', 'Z')) ('S1',) ('Y',) [2] [0]
(('S0', 'S0', 'S2'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S2') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S2'), ('Z', 'Z', 'Z')) ('S2',) ('Z',) [2] [0]
(('S0', 'S0', 'S2'), ('X', 'Z', 'Z')) ('S0', 'S0', 'S2') ('X', 'Z', 'Z')
(('S0', 'S0', 'S2'), ('X', 'Z', 'Z')) ('S2',) ('X',) [2] [0]
(('S0', 'S0', 'S2'), ('Y', 'Z', 'Z')) ('S0', 'S0', 'S2') ('Y', 'Z', 'Z')
(('S0', 'S0', 'S2'), ('Y', 'Z', 'Z')) ('S2',) ('Y',) [2] [0]
(('S0', 'S0', 'S3'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S3') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S3'), ('Z', 'Z', 'Z')) ('S3',) ('Z',) [2] [0]
(('S0', 'S0', 'S3'), ('X', 'Z', 'Z')) ('S0', 'S0', 'S3') ('X', 'Z', 'Z')
(('S0', 'S0', 'S3'), ('X', 'Z', 'Z')) ('S3',) ('X',) [2] [0]
(('S0', 'S0', 'S3'), ('Y', 'Z', 'Z')) ('S0', 'S0', 'S3') ('Y', 'Z', 'Z')
(('S0', 'S0', 'S3'), ('Y', 'Z', 'Z')) ('S3',) ('Y',) [2] [0]
(

In [60]:
for final_bits, fixed_bit_data in frag_data[0].items():
    prep_meas_states, state_counts = zip(*fixed_bit_data.items())
    prep_labels, meas_labels = zip(*prep_meas_states)
    prep_qubit_num = len(prep_labels[0])
    meas_qubit_num = len(meas_labels[0])
    print(prep_qubit_num)

1
1
1
1


In [61]:
len(organized_data)

76

In [62]:
recombined_lists = []
filtered_recombined_lists = []
norm_filtered_lists = []
for i in range(0, num_tomo_circuits):
    direct_models = ml.direct_fragment_model(organized_data[i])
    likely_models = ml.maximum_likelihood_model(direct_models)

    direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map_list[i])
    likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map_list[i])
    recombined_lists.append(likely_recombined_dist)
    filtered_recombined_lists.append(filter_results(likely_recombined_dist, [0]))
    norm_filtered_lists.append(norm_dict(filter_results(likely_recombined_dist, [0])))

{'11': {(('S0',), ('Zp',)): 4965, (('S0',), ('Xm',)): 2470, (('S0',), ('Xp',)): 2594, (('S0',), ('Ym',)): 2478, (('S0',), ('Yp',)): 2510, (('S1',), ('Zp',)): 1697, (('S1',), ('Xp',)): 851, (('S1',), ('Xm',)): 826, (('S1',), ('Ym',)): 834, (('S1',), ('Yp',)): 843, (('S2',), ('Zp',)): 1671, (('S2',), ('Xp',)): 877, (('S2',), ('Xm',)): 778, (('S2',), ('Ym',)): 906, (('S2',), ('Yp',)): 804, (('S3',), ('Zp',)): 1664, (('S3',), ('Xm',)): 859, (('S3',), ('Xp',)): 823, (('S3',), ('Yp',)): 793, (('S3',), ('Ym',)): 833, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '01': {(('S0',), ('Zp',)): 5035, (('S0',), ('Xm',)): 2491, (('S0',), ('Xp',)): 2445, (('S0',), ('Yp',)): 2516, (('S0',), ('Ym',)): 2496, (('S1',), ('Zp',)): 1596, (('S1',), ('Xm',)): 857, (('S1',), ('Xp',)): 774, (('S1',), ('Ym',)): 872, (('S1',), ('Yp',)): 860, (('S2',), ('Zp',)): 1607, (('S2',), ('Xp',)): 810, (('S2',), ('Xm',)): 849, (('S2',), ('Yp',)): 825, (('S2',), ('Ym',)): 835, ((

{'11': {(('S0',), ('Zp',)): 5068, (('S0',), ('Xm',)): 2479, (('S0',), ('Xp',)): 2496, (('S0',), ('Ym',)): 2558, (('S0',), ('Yp',)): 2499, (('S1',), ('Zp',)): 1685, (('S1',), ('Xp',)): 877, (('S1',), ('Xm',)): 807, (('S1',), ('Ym',)): 839, (('S1',), ('Yp',)): 824, (('S2',), ('Zp',)): 1705, (('S2',), ('Xm',)): 885, (('S2',), ('Xp',)): 855, (('S2',), ('Ym',)): 814, (('S2',), ('Yp',)): 860, (('S3',), ('Zp',)): 1737, (('S3',), ('Xp',)): 848, (('S3',), ('Xm',)): 838, (('S3',), ('Yp',)): 851, (('S3',), ('Ym',)): 788, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '01': {(('S0',), ('Zp',)): 4932, (('S0',), ('Xm',)): 2528, (('S0',), ('Xp',)): 2497, (('S0',), ('Yp',)): 2436, (('S0',), ('Ym',)): 2507, (('S1',), ('Zp',)): 1648, (('S1',), ('Xp',)): 841, (('S1',), ('Xm',)): 819, (('S1',), ('Ym',)): 822, (('S1',), ('Yp',)): 824, (('S2',), ('Zp',)): 1595, (('S2',), ('Xm',)): 830, (('S2',), ('Xp',)): 820, (('S2',), ('Ym',)): 867, (('S2',), ('Yp',)): 779, ((

{'01': {(('S0',), ('Zp',)): 4977, (('S0',), ('Xp',)): 2570, (('S0',), ('Xm',)): 2463, (('S0',), ('Ym',)): 2514, (('S0',), ('Yp',)): 2499, (('S1',), ('Zp',)): 1641, (('S1',), ('Xm',)): 763, (('S1',), ('Xp',)): 860, (('S1',), ('Ym',)): 813, (('S1',), ('Yp',)): 856, (('S2',), ('Zp',)): 1649, (('S2',), ('Xm',)): 810, (('S2',), ('Xp',)): 842, (('S2',), ('Ym',)): 873, (('S2',), ('Yp',)): 840, (('S3',), ('Zp',)): 1664, (('S3',), ('Xp',)): 820, (('S3',), ('Xm',)): 823, (('S3',), ('Ym',)): 843, (('S3',), ('Yp',)): 833, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '11': {(('S0',), ('Zp',)): 5023, (('S0',), ('Xm',)): 2501, (('S0',), ('Xp',)): 2466, (('S0',), ('Ym',)): 2455, (('S0',), ('Yp',)): 2532, (('S1',), ('Zp',)): 1638, (('S1',), ('Xm',)): 835, (('S1',), ('Xp',)): 819, (('S1',), ('Ym',)): 828, (('S1',), ('Yp',)): 866, (('S2',), ('Zp',)): 1643, (('S2',), ('Xp',)): 853, (('S2',), ('Xm',)): 839, (('S2',), ('Ym',)): 842, (('S2',), ('Yp',)): 848, ((

{'01': {(('S0',), ('Zp',)): 4989, (('S0',), ('Xp',)): 2575, (('S0',), ('Xm',)): 2455, (('S0',), ('Yp',)): 2504, (('S0',), ('Ym',)): 2488, (('S1',), ('Zp',)): 1665, (('S1',), ('Xm',)): 821, (('S1',), ('Xp',)): 838, (('S1',), ('Ym',)): 799, (('S1',), ('Yp',)): 850, (('S2',), ('Zp',)): 1633, (('S2',), ('Xp',)): 845, (('S2',), ('Xm',)): 858, (('S2',), ('Ym',)): 866, (('S2',), ('Yp',)): 799, (('S3',), ('Zp',)): 1705, (('S3',), ('Xp',)): 852, (('S3',), ('Xm',)): 845, (('S3',), ('Ym',)): 848, (('S3',), ('Yp',)): 841, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '11': {(('S0',), ('Zp',)): 5011, (('S0',), ('Xm',)): 2495, (('S0',), ('Xp',)): 2475, (('S0',), ('Yp',)): 2465, (('S0',), ('Ym',)): 2543, (('S1',), ('Zp',)): 1668, (('S1',), ('Xm',)): 801, (('S1',), ('Xp',)): 856, (('S1',), ('Ym',)): 873, (('S1',), ('Yp',)): 857, (('S2',), ('Zp',)): 1727, (('S2',), ('Xp',)): 847, (('S2',), ('Xm',)): 800, (('S2',), ('Ym',)): 822, (('S2',), ('Yp',)): 826, ((

{'01': {(('S0',), ('Zp',)): 10000, (('S0',), ('Xm',)): 5046, (('S0',), ('Xp',)): 4954, (('S0',), ('Yp',)): 5018, (('S0',), ('Ym',)): 4982, (('S1',), ('Zp',)): 3327, (('S1',), ('Xp',)): 1592, (('S1',), ('Xm',)): 1703, (('S1',), ('Ym',)): 1658, (('S1',), ('Yp',)): 1697, (('S2',), ('Zp',)): 3352, (('S2',), ('Xm',)): 1684, (('S2',), ('Xp',)): 1620, (('S2',), ('Ym',)): 1668, (('S2',), ('Yp',)): 1653, (('S3',), ('Zp',)): 3311, (('S3',), ('Xm',)): 1602, (('S3',), ('Xp',)): 1772, (('S3',), ('Ym',)): 1581, (('S3',), ('Yp',)): 1652, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '10': {(('S1',), ('Zp',)): 6673, (('S1',), ('Xp',)): 3328, (('S1',), ('Xm',)): 3377, (('S1',), ('Ym',)): 3318, (('S1',), ('Yp',)): 3327, (('S2',), ('Zp',)): 6648, (('S2',), ('Xp',)): 3337, (('S2',), ('Xm',)): 3359, (('S2',), ('Yp',)): 3339, (('S2',), ('Ym',)): 3340, (('S3',), ('Zp',)): 6689, (('S3',), ('Xp',)): 3282, (('S3',), ('Xm',)): 3344, (('S3',), ('Yp',)): 3393, (('S3',

...

{'01': {(('S0',), ('Zp',)): 10000, (('S0',), ('Xp',)): 5008, (('S0',), ('Xm',)): 4992, (('S0',), ('Ym',)): 4974, (('S0',), ('Yp',)): 5026, (('S1',), ('Zp',)): 3378, (('S1',), ('Xp',)): 1655, (('S1',), ('Xm',)): 1680, (('S1',), ('Yp',)): 1730, (('S1',), ('Ym',)): 1695, (('S2',), ('Zp',)): 3328, (('S2',), ('Xp',)): 1713, (('S2',), ('Xm',)): 1703, (('S2',), ('Yp',)): 1663, (('S2',), ('Ym',)): 1604, (('S3',), ('Zp',)): 3328, (('S3',), ('Xm',)): 1689, (('S3',), ('Xp',)): 1653, (('S3',), ('Ym',)): 1554, (('S3',), ('Yp',)): 1777, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '10': {(('S1',), ('Zp',)): 6622, (('S1',), ('Xm',)): 3381, (('S1',), ('Xp',)): 3284, (('S1',), ('Yp',)): 3359, (('S1',), ('Ym',)): 3216, (('S2',), ('Zp',)): 6672, (('S2',), ('Xp',)): 3306, (('S2',), ('Xm',)): 3278, (('S2',), ('Yp',)): 3348, (('S2',), ('Ym',)): 3385, (('S3',), ('Zp',)): 6672, (('S3',), ('Xp',)): 3255, (('S3',), ('Xm',)): 3403, (('S3',), ('Yp',)): 3277, (('S3',

{'11': {(('S0',), ('Zp',)): 5076, (('S0',), ('Xp',)): 2514, (('S0',), ('Xm',)): 2518, (('S0',), ('Ym',)): 2456, (('S0',), ('Yp',)): 2510, (('S1',), ('Zp',)): 1668, (('S1',), ('Xm',)): 848, (('S1',), ('Xp',)): 820, (('S1',), ('Yp',)): 826, (('S1',), ('Ym',)): 823, (('S2',), ('Zp',)): 1604, (('S2',), ('Xp',)): 810, (('S2',), ('Xm',)): 871, (('S2',), ('Ym',)): 844, (('S2',), ('Yp',)): 864, (('S3',), ('Zp',)): 1654, (('S3',), ('Xp',)): 859, (('S3',), ('Xm',)): 808, (('S3',), ('Ym',)): 875, (('S3',), ('Yp',)): 805, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '01': {(('S0',), ('Zp',)): 4924, (('S0',), ('Xp',)): 2556, (('S0',), ('Xm',)): 2412, (('S0',), ('Ym',)): 2498, (('S0',), ('Yp',)): 2536, (('S1',), ('Zp',)): 1634, (('S1',), ('Xm',)): 782, (('S1',), ('Xp',)): 831, (('S1',), ('Ym',)): 846, (('S1',), ('Yp',)): 851, (('S2',), ('Zp',)): 1646, (('S2',), ('Xp',)): 847, (('S2',), ('Xm',)): 826, (('S2',), ('Ym',)): 847, (('S2',), ('Yp',)): 829, ((

{'11': {(('S0',), ('Zp',)): 4943, (('S0',), ('Xm',)): 2546, (('S0',), ('Xp',)): 2532, (('S0',), ('Yp',)): 2455, (('S0',), ('Ym',)): 2516, (('S1',), ('Zp',)): 1651, (('S1',), ('Xm',)): 817, (('S1',), ('Xp',)): 846, (('S1',), ('Yp',)): 782, (('S1',), ('Ym',)): 838, (('S2',), ('Zp',)): 1700, (('S2',), ('Xp',)): 827, (('S2',), ('Xm',)): 844, (('S2',), ('Ym',)): 816, (('S2',), ('Yp',)): 855, (('S3',), ('Zp',)): 1709, (('S3',), ('Xm',)): 873, (('S3',), ('Xp',)): 857, (('S3',), ('Yp',)): 791, (('S3',), ('Ym',)): 836, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '01': {(('S0',), ('Zp',)): 5057, (('S0',), ('Xm',)): 2421, (('S0',), ('Xp',)): 2501, (('S0',), ('Ym',)): 2497, (('S0',), ('Yp',)): 2532, (('S1',), ('Zp',)): 1656, (('S1',), ('Xm',)): 801, (('S1',), ('Xp',)): 856, (('S1',), ('Ym',)): 847, (('S1',), ('Yp',)): 828, (('S2',), ('Zp',)): 1670, (('S2',), ('Xp',)): 771, (('S2',), ('Xm',)): 825, (('S2',), ('Ym',)): 838, (('S2',), ('Yp',)): 828, ((

{'01': {(('S0',), ('Zp',)): 10000, (('S0',), ('Xm',)): 4926, (('S0',), ('Xp',)): 5074, (('S0',), ('Yp',)): 4947, (('S0',), ('Ym',)): 5053, (('S1',), ('Zp',)): 3310, (('S1',), ('Xm',)): 1642, (('S1',), ('Xp',)): 1704, (('S1',), ('Ym',)): 1643, (('S1',), ('Yp',)): 1665, (('S2',), ('Zp',)): 3399, (('S2',), ('Xm',)): 1667, (('S2',), ('Xp',)): 1682, (('S2',), ('Yp',)): 1633, (('S2',), ('Ym',)): 1681, (('S3',), ('Zp',)): 3326, (('S3',), ('Xp',)): 1699, (('S3',), ('Xm',)): 1685, (('S3',), ('Yp',)): 1672, (('S3',), ('Ym',)): 1660, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '10': {(('S1',), ('Zp',)): 6690, (('S1',), ('Xp',)): 3348, (('S1',), ('Xm',)): 3306, (('S1',), ('Ym',)): 3377, (('S1',), ('Yp',)): 3315, (('S2',), ('Zp',)): 6601, (('S2',), ('Xp',)): 3345, (('S2',), ('Xm',)): 3306, (('S2',), ('Ym',)): 3428, (('S2',), ('Yp',)): 3258, (('S3',), ('Zp',)): 6674, (('S3',), ('Xp',)): 3299, (('S3',), ('Xm',)): 3317, (('S3',), ('Yp',)): 3273, (('S3',

{'01': {(('S0',), ('Zp',)): 10000, (('S0',), ('Xp',)): 4893, (('S0',), ('Xm',)): 5107, (('S0',), ('Ym',)): 5033, (('S0',), ('Yp',)): 4967, (('S1',), ('Zp',)): 3265, (('S1',), ('Xm',)): 1725, (('S1',), ('Xp',)): 1630, (('S1',), ('Yp',)): 1672, (('S1',), ('Ym',)): 1684, (('S2',), ('Zp',)): 3319, (('S2',), ('Xm',)): 1694, (('S2',), ('Xp',)): 1664, (('S2',), ('Yp',)): 1645, (('S2',), ('Ym',)): 1710, (('S3',), ('Zp',)): 3334, (('S3',), ('Xm',)): 1688, (('S3',), ('Xp',)): 1585, (('S3',), ('Ym',)): 1642, (('S3',), ('Yp',)): 1636, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '10': {(('S1',), ('Zp',)): 6735, (('S1',), ('Xp',)): 3319, (('S1',), ('Xm',)): 3326, (('S1',), ('Yp',)): 3316, (('S1',), ('Ym',)): 3328, (('S2',), ('Zp',)): 6681, (('S2',), ('Xp',)): 3319, (('S2',), ('Xm',)): 3323, (('S2',), ('Ym',)): 3365, (('S2',), ('Yp',)): 3280, (('S3',), ('Zp',)): 6666, (('S3',), ('Xm',)): 3358, (('S3',), ('Xp',)): 3369, (('S3',), ('Yp',)): 3419, (('S3',

In [63]:
# direct_models = ml.direct_fragment_model(frag_data)
# likely_models = ml.maximum_likelihood_model(direct_models)

# direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map)
# likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map)

In [66]:
from utils.utils import filter_results

In [67]:
filter_direct_recombined = filter_results(direct_recombined_dist, [0])

In [68]:

filter_likely_recombined = filter_results(likely_recombined_dist, [0])

In [70]:
norm_filter_dist = norm_dict(filter_likely_recombined)

In [72]:
final_expect_val = 0
for i in range(0, len(pauli_commute)):
    group = pauli_commute[i]
    for Pauli_tuple in group:
        coeff = Pauli_tuple[1]
        final_expect_val += coeff * evaluation(norm_filtered_lists[i], shots = total_counts(norm_filtered_lists[i]), Pauli = Pauli_tuple[0])  

In [74]:
final_expect_val

(-27.869690894241064+0j)

In [75]:
import json
with open('HF_auckland_check0.json', 'w') as f:
    json.dump(norm_filtered_lists, f)

In [76]:
mit = mthree.M3Mitigation(device)
mit.cals_from_file(cals_file = 'mit_data_9_8_14_11_13_12_10_7')

In [77]:
def update_dict(quasis, total_shots = None):
    for key in quasis.keys():
        quasis[key] = quasis[key]*total_shots

In [78]:
mit_lists = []
for i in range(0, len(pauli_commute)):
    total_shots = total_counts(norm_filtered_lists[i])
    quasis = mit.apply_correction(norm_filtered_lists[i], [9,8,14,11,13,12,10,7])
    update_dict(quasis, total_shots = total_shots)
    mit_lists.append(quasis)

In [79]:
miti_expect_val = 0
for i in range(0, len(pauli_commute)):
    group = pauli_commute[i]
    for Pauli_tuple in group:
        coeff = Pauli_tuple[1]
        miti_expect_val += coeff * evaluation(mit_lists[i], shots = total_counts(mit_lists[i]), Pauli = Pauli_tuple[0]) 
miti_expect_val

(-28.079530425572063+0j)

In [80]:
with open('HF_auckland_check0_mit.json', 'w') as f:
    json.dump(mit_lists, f)